In [22]:
import pandas as pd
import json 
import os
import numpy as np

import warnings
warnings.filterwarnings("ignore")

## Phases of play
### How to obtain these 4 phases ?

![](../assets/images/Phases_of_play.png)

Pistes : 
- https://www.statsperform.com/resource/phases-of-play-an-introduction/ 


In [23]:
data_directory = '../data/StatsBomb'
df_events = list()

## Concaténation de tous les matchs 
for file in os.listdir(data_directory) :
    # Sélection des données d'évènements
    if 'events.json' in file : 
        #match_events_path = os.path.join(data_directory, file)
        match_events_path = os.path.join(data_directory,"ManCity_AstonVilla_events.json")
    else :
        continue
    # Lecture du json
    with open(match_events_path) as json_file:
        match_events = json.load(json_file)
    # Ajout du dataframe obtenu
    df_events.append(pd.read_json(match_events_path))
    break
df_events = pd.concat(df_events)

In [24]:
df_events.columns

Index(['id', 'index', 'period', 'timestamp', 'minute', 'second', 'type',
       'possession', 'possession_team', 'play_pattern', 'obv_for_after',
       'obv_for_before', 'obv_for_net', 'obv_against_after',
       'obv_against_before', 'obv_against_net', 'obv_total_net', 'team',
       'duration', 'tactics', 'related_events', 'player', 'position',
       'location', 'pass', 'carry', 'under_pressure', 'ball_receipt',
       'interception', 'counterpress', 'clearance', 'shot', 'out',
       'goalkeeper', 'duel', '50_50', 'off_camera', 'dribble', 'block',
       'ball_recovery', 'foul_won', 'injury_stoppage', 'substitution',
       'foul_committed'],
      dtype='object')

In [25]:
df_events.loc[:, 'play_pattern_id'] = df_events.play_pattern.apply(lambda x: x['id'])
df_events.loc[:, 'possession_team_id'] = df_events.possession_team.apply(lambda x: x['id'])
df_events.loc[:, 'team_id'] = df_events.team.apply(lambda x: x['id'])
df_events.loc[:, 'type_id'] = df_events.type.apply(lambda x: x['id'])

df_events.loc[~df_events.player.isna(), 'player_id'] = df_events.loc[~df_events.player.isna(), 'player'].apply(lambda x: x['id'])

df_events.loc[~df_events.location.isna(), 'x'] = df_events.loc[~df_events.location.isna(), 'location'].apply(lambda x : x[0])
df_events.loc[~df_events.location.isna(), 'y'] = df_events.loc[~df_events.location.isna(), 'location'].apply(lambda x : x[1])

In [26]:
min_possession_length = 0

# On ne considère uniquement les séquences de longueur supérieure à 3 ? 
# Longueur d'une possession
df_events.loc[:, 'possession_length'] = df_events.groupby('possession').id.transform('count')
df_events = df_events[df_events.possession_length >= min_possession_length]

# Suppression des coups de pieds arrétés et corner
#df_events = df_events[~df_events.play_pattern_id.isin((2, 3))]

# On ne s'intéresse qu'à ManCity ? 
df_events = df_events[df_events.possession_team_id == 746]

In [27]:
play_phase = {
    1 : 'Build-up play',
    2 : 'Counter-attacking',
    3 : 'Final third penetration and finishing'
}

# Build-up play
# Toutes les actions qui débutent dans la moitié de terrain de l'équipe
df_events.loc[df_events.x < 60, 'play_phase_id'] = 1

# Final third penetration and finishing
# Action dans le dernier tiers 
df_events.loc[df_events.x > 80, 'play_phase_id'] = 3

# Counter-attacking
# L'id 6 de play_pattern tague directement les contres-attaques
df_events.loc[df_events.play_pattern_id == 6, 'play_phase_id'] = 2

## Viz

In [28]:
import plotly.graph_objects as go
import sys
from PIL import Image

sys.path.insert(0, '../')
from scripts.viz import create_field

In [29]:
df_events_finishing = df_events[df_events.play_phase_id == 3]
df_events_finishing = df_events_finishing[df_events_finishing.minute <= 55]

# Actions à au moins deux passes
df_events_finishing.possesion_length = df_events_finishing.groupby('possession').id.transform('count')
df_events_finishing = df_events_finishing[df_events_finishing.possesion_length >= 2]

# Actions uniquement de Man City
df_events_finishing = df_events_finishing[df_events_finishing.team_id == 746]

# Position moyenne des joueurs
player_position = df_events_finishing.groupby(['player_id'])[['x', 'y']].mean().reset_index().dropna()

# Passes et valeurs
pass_events = df_events_finishing[df_events_finishing.type_id == 30] 
pass_events.loc[:, 'recept_player_id'] = pass_events['pass'].apply(lambda x : x['recipient']['id'] if 'recipient' in x else None)

pass_events = pass_events.merge(player_position, right_on = 'player_id', left_on = 'player_id')
pass_events = pass_events.merge(player_position, right_on = 'player_id', left_on = 'recept_player_id')
pass_events.loc[:, 'impact'] = pass_events.groupby(['player_id_x', 'recept_player_id']).obv_for_net.transform('sum')
pass_events.loc[:, 'impact2'] = pass_events.groupby(['player_id_x', 'recept_player_id']).obv_for_net.transform('count')

pass_events.impact = (pass_events.impact - pass_events.impact.min()) / (pass_events.impact.max() - pass_events.impact.min())

pass_events = pass_events[['player_id_x', 'recept_player_id', 'x_y', 'y_y', 'x', 'y', 'impact', 'impact2']].drop_duplicates()

#pass_events = pass_events[pass_events.player_id_x == 25632]
#pass_events = pass_events[pass_events.recept_player_id == 25632]


In [30]:
ARROW_SHIFT = 1
jaune = 235, 254, 83
bleu = 105, 207, 249
violet = 167, 75, 223

def plot_players(fig, player_position):
    """"""
    for x, y, id in zip(player_position.x, player_position.y, player_position.player_id) :
        fig.add_layout_image(dict(
            source= Image.open(f"../assets/images/players/{int(id)}.png"),
            xref="x",
            yref="y",
            x=x,
            y= y + 1.25,
            sizex=8,
            sizey=8,
            xanchor="center",
            yanchor="middle",
            )
        )
    fig.add_traces(go.Scatter(
        x = player_position.x, 
        y = player_position.y, 
        mode="markers",
        marker_line_color=f'rgba({255}, {255}, {255}, 1)', 
        marker_color='rgba(255, 255, 255, 0)',
        marker_line_width = 3, 
        marker_size = 30
        )
    )
    return fig 

def plot_passes(fig, pass_events):
    """"""
    for x1, y1, x2, y2, impact, impact2 in zip(pass_events.x_y, pass_events.y_y, pass_events.x, pass_events.y, pass_events.impact, pass_events.impact2):
        ortho_vec = np.array((y2-y1,x2-x1))
        ortho_vec = ortho_vec / np.linalg.norm(ortho_vec)
        x_shift, y_shift = ARROW_SHIFT * ortho_vec    
        
        fig.add_annotation(
            x = x1 + x_shift,  # arrows' head
            y = y1 + y_shift,  # arrows' head
            ax = x2 + x_shift,  # arrows' tail
            ay = y2 + y_shift,  # arrows' tail
            xref='x',
            yref='y',
            axref='x',
            ayref='y',
            showarrow=True,
            arrowhead=2,
            standoff = 15,
            startstandoff = 5,
            arrowwidth=2,
            arrowcolor=f'rgba({bleu[0]}, {bleu[1]}, {bleu[2]}, {impact2 / pass_events.impact2.max()})'
        )
    return fig 

fig = create_field()
fig = plot_players(fig, player_position)
fig = plot_passes(fig, pass_events)


fig.update_layout(
    showlegend=False,
    autosize=True,
    margin=dict(l=20, r=20, t=20, b=20),
    width=600,
    height=400,
    plot_bgcolor = 'rgba(31, 29, 43, 1)' ,
    paper_bgcolor = 'rgba(31, 29, 43, 1)' 
    )

fig.update_xaxes(showgrid=False, zeroline = False, visible = False)
fig.update_yaxes(showgrid=False, zeroline = False, visible = False)

fig.show()